In [1]:
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity
import pandas as pd
import numpy as np
import json
import re
import itertools

In [2]:
df_nickname = pd.read_csv('nicknames.csv')

In [3]:
df_nickname

nick_name
0                       NaN
1          ‌ ‌ ‌ ‌ ‌ ‌ ‌ ‌?
2           ‌ ‌ ‌- emilia<3
3        ⁭⁫⁪⁫⁬⁭⁫⁪⁫⁬ ⁭hop_pa
4                     ‌ (Z)
...                     ...
141246        𝓜𝓸𝓱𝓪𝓶𝓶𝓪𝓭 𝓡𝓮𝔃𝓪
141247         🤍🖤🤎💜💙💚💛🧡⁦❤️⁩
141248            𝐌𝐚𝐫𝐳𝐢𝐲𝐞𝐡🌱
141249           𝓐𝓶𝓲𝓻𝓱𝓸𝓼𝓮𝓲𝓷
141250          𝒎𝒂𝒉𝒅𝒐𝒌𝒉𝒕𝒂𝒓𝒚

[141251 rows x 1 columns]

In [4]:
df_nickname.dropna(inplace=True)

In [5]:
df_sw_en = pd.read_csv('bad-words.csv')

df_sw_en = df_sw_en.rename(columns={"jigaboo":"word"})

In [6]:
df_sw_fa = pd.read_json("data.json")

In [7]:
df_sw_fa = pd.concat([df_sw_fa, pd.DataFrame({'word':['اینستاگرام', 'اینستا', 'تلگرام', 'واتساپ','روبیکا', 'تماس', 'زنگ', 'بزنگ','telegram', 'whatsapp', 'insta', 'instagram','رل','ایدی', 'تل','وات','فاک']})])

In [8]:
df_sw = pd.concat([df_sw_en, df_sw_fa])

In [9]:
df_sw.dropna(inplace=True)

In [10]:
words = df_sw['word'].astype(str).tolist()

In [11]:
def tokenize(word):
    re_pattern = r'\b\w+\b'
    words = re.findall(re_pattern, word)
    return words

In [12]:
df_nickname['tokens'] = df_nickname['nick_name'].apply(tokenize)

In [13]:
df_nickname

nick_name            tokens
1          ‌ ‌ ‌ ‌ ‌ ‌ ‌ ‌?                []
2           ‌ ‌ ‌- emilia<3       [emilia, 3]
3        ⁭⁫⁪⁫⁬⁭⁫⁪⁫⁬ ⁭hop_pa          [hop_pa]
4                     ‌ (Z)               [Z]
5                   ‍ Azita           [Azita]
...                     ...               ...
141246        𝓜𝓸𝓱𝓪𝓶𝓶𝓪𝓭 𝓡𝓮𝔃𝓪  [𝓜𝓸𝓱𝓪𝓶𝓶𝓪𝓭, 𝓡𝓮𝔃𝓪]
141247         🤍🖤🤎💜💙💚💛🧡⁦❤️⁩                []
141248            𝐌𝐚𝐫𝐳𝐢𝐲𝐞𝐡🌱        [𝐌𝐚𝐫𝐳𝐢𝐲𝐞𝐡]
141249           𝓐𝓶𝓲𝓻𝓱𝓸𝓼𝓮𝓲𝓷      [𝓐𝓶𝓲𝓻𝓱𝓸𝓼𝓮𝓲𝓷]
141250          𝒎𝒂𝒉𝒅𝒐𝒌𝒉𝒕𝒂𝒓𝒚     [𝒎𝒂𝒉𝒅𝒐𝒌𝒉𝒕𝒂𝒓𝒚]

[141248 rows x 2 columns]

In [14]:
def find_swear(tokens):
    print(f'Proccessing {tokens}', end='\t')
    for word in words:
        if word in tokens:
            print(f"====> {word} is swear" )
            return word
    for token in tokens:
        mobile_pattern = r'^(\+98|0)?9\d{9}$'
        email_pattern = r'([A-Za-z0-9]+[.-_])*[A-Za-z0-9]+@[A-Za-z0-9-]+(\.[A-Z|a-z]{2,})+'
        mobile_found = re.findall(mobile_pattern, token)
        email_found = re.match(email_pattern, token)
        if mobile_found or email_found:
            return 'contact_info'
    print('\n')
    return 0

In [15]:
df_nickname['is_swear'] = df_nickname['tokens'].apply(find_swear)

Proccessing []	

Proccessing ['emilia', '3']	

Proccessing ['hop_pa']	

Proccessing ['Z']	

Proccessing ['Azita']	

Proccessing ['Baran']	

Proccessing ['Behzad']	

Proccessing ['farhad']	

Proccessing ['fatem']	

Proccessing ['hodayseh']	

Proccessing ['kamyarkrban']	

Proccessing ['MahdisBahadori']	

Proccessing ['mohamad1389']	

Proccessing ['nazanin']	

Proccessing ['pourya']	

Proccessing ['Rahi']	

Proccessing ['Rawuf']	

Proccessing ['somi']	

Proccessing ['Weirdo']	

Proccessing ['zeynab']	

Proccessing ['امیدفاضلی']	

Proccessing ['علیرضا']	

Proccessing ['فاطمه']	

Proccessing ['月亮', 'fafa']	

Proccessing ['로자']	

Proccessing ['ـ']	

Proccessing ['ــ']	

Proccessing ['ــ', 'T']	

Proccessing ['ـــ']	

Proccessing ['ــــ']	

Proccessing ['ـــــــ']	

Proccessing ['ــــــــ']	

Proccessing ['ــــــــــــــ']	

Proccessing ['ــــــــــــــــــــ']	

Proccessing ['ـــ']	

Proccessing ['ــMARZieh']	

Proccessing ['ــZahra']	

Proccessing ['ـ', 'ـ', 'تاجكم', 'źǺHяǺ', 'ـ', 'ـ']	

Pr

Proccessing ['a', 'haaland']	

Proccessing ['A', 'Hadadi']	

Proccessing ['A', 'HADI']	

Proccessing ['A', 'hairan']	

Proccessing ['A', 'hasanvand']	

Proccessing ['a', 'hashemi']	

Proccessing ['a', 'hashemzadeh']	

Proccessing ['A', 'hb']	

Proccessing ['A', 'hbi']	

Proccessing ['a', 'hgbin']	

Proccessing ['A', 'hip1400']	

Proccessing ['A', 'hmd']	

Proccessing ['A', 'hmd_s']	

Proccessing ['A', 'ho3ein']	

Proccessing ['A', 'Hojaji']	

Proccessing ['a', 'homayounmehr7373']	

Proccessing ['A', 'hosseini']	

Proccessing ['A', 'hr']	

Proccessing ['A', 'hs']	

Proccessing ['A', 'HTM']	

Proccessing ['a', 'hz']	

Proccessing ['a', 'i', 'd', 'i', 'n', '138999']	

Proccessing ['a', 'i', 'r', 'a', 'a', 'i']	

Proccessing ['a', 'j']	

Proccessing ['A', 'J_AMIR⁵¹']	

Proccessing ['A', 'j', 'gork']	

Proccessing ['a', 'j', '1400']	

Proccessing ['A', 'JA', '2']	

Proccessing ['a', 'jafari']	

Proccessing ['A', 'jahanzade']	

Proccessing ['a', 'judy']	

Proccessing ['a', 'k']	

Proccessing

Proccessing ['Aliahmadjafary']	

Proccessing ['aliahmadrahimi']	

Proccessing ['AliAhmadzadeh']	

Proccessing ['aliahmed']	

Proccessing ['Aliahmt83']	

Proccessing ['AliAhoo']	

Proccessing ['aliahora']	

Proccessing ['aliaj']	

Proccessing ['Aliajdari']	

Proccessing ['aliajf']	

Proccessing ['aliakbaer']	

Proccessing ['AliAkbar']	

Proccessing ['ALIAKBAR', '92']	

Proccessing ['ALiakbar', 'Abayat']	

Proccessing ['aliakbar', 'fazli']	

Proccessing ['aliakbar', 'kamali']	

Proccessing ['Aliakbar', 'Khanzad']	

Proccessing ['Aliakbar', 'mehdipoor']	

Proccessing ['aliakbar', 'mousavi']	

Proccessing ['Aliakbar', 'parsa']	

Proccessing ['aliakbar', 'rezaei']	

Proccessing ['Aliakbar_']	

Proccessing ['aliakbar_ahmadi']	

Proccessing ['Aliakbar', 'Kabirinia']	

Proccessing ['aliakbar', 'barez']	

Proccessing ['aliakbar', 'gls']	

Proccessing ['aliakbar', 'hoseeny']	

Proccessing ['aliakbar', 'hosseini']	

Proccessing ['Aliakbar0062']	

Proccessing ['aliakbar1000']	

Proccessing ['Aliak

Proccessing ['Ar6iN']	

Proccessing ['AR7']	

Proccessing ['ar7hang']	

Proccessing ['ar7inn']	

Proccessing ['AR9']	

Proccessing ['Ar90']	

Proccessing ['AR9222']	

Proccessing ['ARA']	

Proccessing ['ara', 'ghanemi']	

Proccessing ['ARA1990']	

Proccessing ['ara75']	

Proccessing ['Araaam']	

Proccessing ['Araah']	

Proccessing ['araam']	

Proccessing ['Araam_shl']	

Proccessing ['Araas']	

Proccessing ['arab']	====> {word} is swear
Proccessing ['arab', 'boy']	====> {word} is swear
Proccessing ['arab106']	

Proccessing ['arabedi']	

Proccessing ['arabi', '83']	

Proccessing ['Arabic']	

Proccessing ['Arabkuhsar']	

Proccessing ['Arabo']	

Proccessing ['arabzade']	

Proccessing ['arad']	

Proccessing ['Arad', '_Kurd']	

Proccessing ['Arad', 'Babaei']	

Proccessing ['arad', 'bideh']	

Proccessing ['Arad', 'Poortaghi']	

Proccessing ['arad', 'safa']	

Proccessing ['Arad', 'sayyadi']	

Proccessing ['Arad_Jahandideh']	

Proccessing ['arad_rd']	

Proccessing ['Arad_SH']	

Proccessing ['Ar

Proccessing ['best', 'player']	

Proccessing ['BEST', 'SKY']	

Proccessing ['best', 'user']	

Proccessing ['best_mechanical_boy']	

Proccessing ['Best', 'trader']	

Proccessing ['best2020']	

Proccessing ['BestLordInWorld']	

Proccessing ['BestMan']	

Proccessing ['beststar']	

Proccessing ['BETA']	

Proccessing ['Betavash']	

Proccessing ['Bete']	

Proccessing ['BETER']	

Proccessing ['beth']	

Proccessing ['beti']	

Proccessing ['beti7110']	

Proccessing ['Betida']	

Proccessing ['beto', 'che']	

Proccessing ['Beto0oche']	

Proccessing ['betoche']	

Proccessing ['better', 'call', 'mehdi']	

Proccessing ['betty']	

Proccessing ['betty_kh']	

Proccessing ['bety']	

Proccessing ['Beuiamiu']	

Proccessing ['beuti']	

Proccessing ['bewar']	

Proccessing ['bex']	

Proccessing ['bey']	

Proccessing ['beyan']	

Proccessing ['Beyg']	

Proccessing ['beygi']	

Proccessing ['Beygrezaii']	

Proccessing ['beyk']	

Proccessing ['beykifarani']	

Proccessing ['beykii']	

Proccessing ['beyond']	

Proc

...

Proccessing ['سید', 'نسیم']	

Proccessing ['سید', 'نصرالله', 'ابوالحسنی']	

Proccessing ['سید', 'نصراله']	

Proccessing ['سید', 'نعیم', 'موسوی']	

Proccessing ['سید', 'نفیس', 'سادات']	

Proccessing ['سید', 'نور', 'الحسن', 'عابدی']	

Proccessing ['سید', 'نوید']	

Proccessing ['سید', 'نیما']	

Proccessing ['سید', 'نیما', 'موسوی']	

Proccessing ['سید', 'هادی']	

Proccessing ['سید', 'هادی', 'جلیلیان']	

Proccessing ['سید', 'هادی', 'رفیعی']	

Proccessing ['سید', 'هادی', 'رنجبر']	

Proccessing ['سید', 'هادی', 'قهاری']	

Proccessing ['سید', 'هادی', 'محمودی']	

Proccessing ['سید', 'هادی', 'موسوی']	

Proccessing ['سید', 'هادی', 'هاشمی']	

Proccessing ['سید', 'هاشم']	

Proccessing ['سید', 'هاشم', 'شریفی']	

Proccessing ['سید', 'هاشم', 'غرابی']	

Proccessing ['سید', 'هاشم', 'محمداصل']	

Proccessing ['سید', 'هاشمی']	

Proccessing ['سید', 'هانی', 'سیدی']	

Proccessing ['سید', 'هدایت', 'اله', 'فقیه']	

Proccessing ['سید', 'هدیه']	

Proccessing ['سید', 'همایون', 'حق', 'بجانب']	

Proccessing ['سی', 'د

Proccessing ['علیرضا', 'لعلی', 'سراب']	

Proccessing ['علیرضا', 'متقی']	

Proccessing ['علیرضا', 'متین', 'فر']	

Proccessing ['علیرضا', 'محسنی']	

Proccessing ['علیرضا', 'محمدی']	

Proccessing ['علیرضا', 'محمدی', 'الموتی']	

Proccessing ['علیرضا', 'محمدی', 'کردخیلی']	

Proccessing ['علیرضا', 'محمودی']	

Proccessing ['علیرضا', 'مرادی']	

Proccessing ['علیرضا', 'مرادی', 'فرد']	

Proccessing ['علیرضا', 'مروت']	

Proccessing ['علیرضا', 'مزرعاوی']	

Proccessing ['علیرضا', 'مسعودی']	

Proccessing ['علیرضا', 'مظاهری']	

Proccessing ['علیرضا', 'مظلومی']	

Proccessing ['علیرضا', 'معتضدیان']	

Proccessing ['علیرضا', 'مقدم']	

Proccessing ['علیرضا', 'ملایی']	

Proccessing ['علیرضا', 'ملکی']	

Proccessing ['علیرضا', 'منصوری']	

Proccessing ['علیرضا', 'مهرابی']	

Proccessing ['علیرضا', 'مهرافشار']	

Proccessing ['علیرضا', 'موتاب', 'حسن', 'دخت']	

Proccessing ['علیرضا', 'مولازاده']	

Proccessing ['علیرضا', 'مومنی']	

Proccessing ['علیرضا', 'میر']	

Proccessing ['علیرضا', 'میربزرگ']	

Proccessing ['ع

Proccessing ['مجتبی', 'طافی']	

Proccessing ['مجتبی', 'طالع', 'زاری']	

Proccessing ['مجتبی', 'طاهری']	

Proccessing ['مجتبی', 'عباسی']	

Proccessing ['مجتبی', 'عبداللهی']	

Proccessing ['مجتبی', 'عثمانی']	

Proccessing ['مجتبی', 'عزیزی']	

Proccessing ['مجتبی', 'علوی']	

Proccessing ['مجتبی', 'علی', 'اکبری']	

Proccessing ['مجتبی', 'علی', 'حسینی']	

Proccessing ['مجتبی', 'علیزاده']	

Proccessing ['مجتبی', 'غیور']	

Proccessing ['مجتبی', 'فاتحی']	

Proccessing ['مجتبی', 'فلاح']	

Proccessing ['مجتبی', 'فیرزومنش']	

Proccessing ['مجتبی', 'فیروز']	

Proccessing ['مجتبی', 'قاسمپور']	

Proccessing ['مجتبی', 'قاسمی']	

Proccessing ['مجتبی', 'قدسی']	

Proccessing ['مجتبی', 'قربانی']	

Proccessing ['مجتبی', 'قنبری']	

Proccessing ['مجتبی', 'کاشی']	

Proccessing ['مجتبی', 'کاظمپور']	

Proccessing ['مجتبی', 'کاویانی']	

Proccessing ['مجتبی', 'کبیری']	

Proccessing ['مجتبی', 'کرمی']	

Proccessing ['مجتبی', 'گنجعلی']	

Proccessing ['مجتبی', 'لشگری']	

Proccessing ['مجتبی', 'مباشری']	

Proccessing

Proccessing ['مصطفی', 'بزرگزاده']	

Proccessing ['مصطفی', 'بلواسی']	

Proccessing ['مصطفی', 'بیابانی']	

Proccessing ['مصطفی', 'بیات']	

Proccessing ['مصطفی', 'بیت', 'سیاح']	

Proccessing ['مصطفی', 'پازکی']	

Proccessing ['مصطفی', 'پرده', 'نشین']	

Proccessing ['مصطفی', 'پژمانفر']	

Proccessing ['مصطفی', 'پورمحمودی']	

Proccessing ['مصطفی', 'تاجیک']	

Proccessing ['مصطفی', 'توکلی']	

Proccessing ['مصطفی', 'تیموری']	

Proccessing ['مصطفی', 'جان']	

Proccessing ['مصطفی', 'جاویده']	

Proccessing ['مصطفی', 'جراحی']	

Proccessing ['مصطفی', 'جعفری']	

Proccessing ['مصطفی', 'جمشیدی']	

Proccessing ['مصطفی', 'جهانی']	

Proccessing ['مصطفی', 'چشم', 'براه']	

Proccessing ['مصطفی', 'چمران']	

Proccessing ['مصطفی', 'حائری']	

Proccessing ['مصطفی', 'حاتمی']	

Proccessing ['مصطفی', 'حاجلو']	

Proccessing ['مصطفی', 'حسن', 'زاده']	

Proccessing ['مصطفی', 'حسینی']	

Proccessing ['مصطفی', 'حشمتی']	

Proccessing ['مصطفی', 'حقیقت']	

Proccessing ['مصطفی', 'حمزه']	

Proccessing ['مصطفی', 'خادمی']	

Procces

Proccessing ['هانیه', 'محمدی']	

Proccessing ['هانیه', 'محمودی']	

Proccessing ['هانیه', 'مرادی']	

Proccessing ['هانیه', 'مصلایی']	

Proccessing ['هانیه', 'ملاویسی']	

Proccessing ['هانیه', 'منصوری']	

Proccessing ['هانیه', 'مهربد']	

Proccessing ['هانیه', 'میرزایی']	

Proccessing ['هانیه', 'نژادی']	

Proccessing ['هانیه', 'هاشمی']	

Proccessing ['هانیه', 'وفایی', 'نژاد']	

Proccessing ['هانیه', 'یارمحمدی']	

Proccessing ['هانیهبختیاری']	

Proccessing ['هانیه', 'زاغی']	

Proccessing ['هاه']	

Proccessing ['هاوار']	

Proccessing ['هاوبیر', 'معروفی']	

Proccessing ['هاوره']	

Proccessing ['هاوری']	

Proccessing ['هاوری', 'کاردانی']	

Proccessing ['هاوری', 'کافی']	

Proccessing ['هاوری', 'محمدی']	

Proccessing ['هاوژین']	

Proccessing ['هاوژین', 'ابراهیمی']	

Proccessing ['هاوژین', 'رسولی', 'کانی', 'بلاغ']	

Proccessing ['هاوژین', 'محمد', 'امین']	

Proccessing ['هاوژین', 'محمودی']	

Proccessing ['هاوکار']	

Proccessing ['هاوناز', 'کریمی']	

Proccessing ['هاوین']	

Proccessing ['هايدر']	


In [16]:
swears = df_nickname[df_nickname['is_swear']!=0]

In [17]:
len(swears)

861

In [18]:
swears.to_csv('swears.csv')

In [77]:
pattern = r'([A-Za-z0-9]+[.-_])*[A-Za-z0-9]+@[A-Za-z0-9-]+(\.[A-Z|a-z]{2,})+'

In [81]:
res = re.match(pattern, 'mrph@gmail.com')

In [82]:
res.group(0)

'mrph@gmail.com'